This notebook intents to implement the "HYPERSPECTRAL BAND SELECTION BASED ON GRAPH CLUSTERING" paper by Hedjam & Cheriet. 

First the necesary libraries will be imported.

In [1]:
import numpy as np
import cv2
import matplotlib.pyplot as plt
from scipy.io import loadmat

The next funtion reads the hyperspectral images from matlab format to numpy array. 

In [2]:
def read_HSI():
    X = loadmat('Indian_pines_corrected.mat')['indian_pines_corrected']
    y = loadmat('Indian_pines_gt.mat')['indian_pines_gt']
    #print(f"X shape: {X.shape}\ny shape: {y.shape}")
    return X, y

In [3]:
(corrected,ground_truth) = read_HSI()

The next cell defines functions for  taking an sxs part of an image and getting its histogram from all the image

In [4]:
def h_mask(s, b, bins):
    '''
    This function takes in a matrix b representing a hyperspectral band and applies a sxs histogram mask to it.
    @s sixe of sxs mask
    @b band to apply.
    '''
    (width_b, heigth_b) = b.shape
    
    
    if s >= width_b or s>= heigth_b:
        return 0
    
    pad = (s-1)//2
    
    output = np.zeros((width_b-s+1, heigth_b-s+1,bins))
    h = np.zeros((bins))
    
    for y in np.arange(pad, heigth_b - pad):
        for x in np.arange(pad, width_b - pad):
            # extract the RegionOfInterest of the image by extracting the
            # *center* region of the current (x, y)-coordinates
            # dimensions
            roi = b[y - pad:y + pad + 1, x - pad:x + pad + 1]
            # perform the actual convolution by taking the
            # element-wise multiplicate between the ROI and
            # the kernel, then summing the matrix
            (h,_) = np.histogram(roi, bins=bins)
            #histogram normalization
            #print(h)
            #print(np.linalg.norm(h))
            h = h/np.linalg.norm(h)
            #print(h)
            # store the convolved value in the output (x,y)-
            # coordinate of the output image
            output[y - pad, x - pad,:] = h
            
            
    return output
    
    
    

In [26]:
#print(Hyper_histogram_filter.shape)
print(Hyper_histogram_filter.shape)
print(Hyper_histogram_filter[45,45,3,:])

(139, 139, 200, 10)
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]


The bhattacharyya distance is a statistical tool to know the relation between two different distributions.

In [34]:
def bhattacharyya(dist_a,dist_b):
    #print("dista_pre---> ",dist_a)
    #print("distb_pre---> ",dist_b)
    dist_a = dist_a**(1/2)
    #print("dista--->",dist_a)
    dist_b = dist_b**(1/2)
    #print("distb---> ",dist_b)
    m=np.multiply(dist_a,dist_b)
    #print("m---> ",m)
    s=1-np.sum(m)
    #print("s---> ",s)
    bhatt=np.abs(s)**(1/2)
    print("Bhatt: ",bhatt)
    
    return bhatt

Here the Battacharyya distance will be applied to form a similarity matrix matrix "Corr_m" where each 

In [35]:
def bhatt_integrate(band1, band2):
    
    (height, width, _) = band1.shape
    
    integrate = 0
    
    for i in range(height):
        
        for j in range(width):
            
            integrate += bhattacharyya(band1[i,j],band2[i,j])
            print("valor integral: ", integrate)
    return integrate

In [45]:
def bhatt_simil_matrix(hhm):
    '''
    
    @hhm hyperspectral histrogram matrix. matrix of the form (xpixels, ypixels, #bands, histogramSize)
    '''
    #Taking dimension out of hhm. 
    (height, width, bands,_) = hhm.shape
    #declaration of the correlation matrix, which must be #bandsX#bands. 
    Corr_m = np.zeros((bands, bands))
    
    #iterates over resulting correlation matrix to save result of each band comparison
    for i in range(bands):
        for j in range(i+1, bands):
            if i == j :
                continue
            Corr_m[i,j] = bhatt_integrate(hhm[:,:,i,:],hhm[:,:,j,:])
    
    return Corr_m

Here the histogram for every band is applies to every band of the hyperspectral image as a sxs filter. And a new array is created containing the histogram vectors. 

In [46]:
#MAIN

(corrected,ground_truth) = read_HSI()

#def hyper_filter():
(Wc, Hc, Dc) = corrected.shape

bins = 10

filter_size = 7

Hyper_histogram_filter = np.zeros((Wc-filter_size+1, Hc-filter_size+1,Dc,bins))

for i in range(3):
    Hyper_histogram_filter[:,:,i,:] = h_mask(filter_size,corrected[:,:,i], bins)

Correlation_matrix = bhatt_simil_matrix(Hyper_histogram_filter)

np.savetxt('Correlation_matrix.txt', Correlation_matrix)

0
1
2
1
Bhatt:  0.722549078792652
valor integral:  0.722549078792652
Bhatt:  0.6638227315641068
valor integral:  1.3863718103567586
Bhatt:  0.3539115747277755
valor integral:  1.740283385084534
Bhatt:  0.36898755714526554
valor integral:  2.1092709422297995
Bhatt:  0.5688764330768259
valor integral:  2.6781473753066254
Bhatt:  0.6238434283592248
valor integral:  3.3019908036658503
Bhatt:  0.58479748164919
valor integral:  3.88678828531504
Bhatt:  0.5675679617272501
valor integral:  4.45435624704229
Bhatt:  0.5542002724629762
valor integral:  5.008556519505267
Bhatt:  0.7094771668205052
valor integral:  5.718033686325772
Bhatt:  0.6753462815871993
valor integral:  6.3933799679129715
Bhatt:  0.5723843966720551
valor integral:  6.965764364585026
Bhatt:  0.5005842385443706
valor integral:  7.466348603129397
Bhatt:  0.5832182341529693
valor integral:  8.049566837282367
Bhatt:  0.3875262124794015
valor integral:  8.437093049761769
Bhatt:  0.5432452559224932
valor integral:  8.980338305684262

Bhatt:  0.6092813597159119
valor integral:  245.7605836236564
Bhatt:  0.8534482820044901
valor integral:  246.61403190566088
Bhatt:  0.8007188209760018
valor integral:  247.4147507266369
Bhatt:  0.6348302794989417
valor integral:  248.04958100613584
Bhatt:  0.605294542081583
valor integral:  248.65487554821743
Bhatt:  0.5529531351537069
valor integral:  249.20782868337113
Bhatt:  0.4042722440108762
valor integral:  249.61210092738202
Bhatt:  0.6344383189747275
valor integral:  250.24653924635675
Bhatt:  0.6452156233936677
valor integral:  250.8917548697504
Bhatt:  0.3181258437616217
valor integral:  251.20988071351204
Bhatt:  0.0579129110174886
valor integral:  251.26779362452953
Bhatt:  0.5711070123389838
valor integral:  251.83890063686852
Bhatt:  0.49467225607633397
valor integral:  252.33357289294486
Bhatt:  0.42255485237457974
valor integral:  252.75612774531945
Bhatt:  0.31943069469803875
valor integral:  253.0755584400175
Bhatt:  0.6034686448048888
valor integral:  253.679027084

valor integral:  528.2443296742446
Bhatt:  0.4642126662237727
valor integral:  528.7085423404683
Bhatt:  0.4036344248699598
valor integral:  529.1121767653383
Bhatt:  0.6576147887742805
valor integral:  529.7697915541125
Bhatt:  0.6875027969185878
valor integral:  530.4572943510311
Bhatt:  0.6636009697947594
valor integral:  531.1208953208259
Bhatt:  0.6690859218757569
valor integral:  531.7899812427016
Bhatt:  0.6545842368117523
valor integral:  532.4445654795134
Bhatt:  0.9519384454880916
valor integral:  533.3965039250014
Bhatt:  0.37683637783318924
valor integral:  533.7733403028346
Bhatt:  0.42186265545999696
valor integral:  534.1952029582947
Bhatt:  0.27775218271902125
valor integral:  534.4729551410137
Bhatt:  0.31966107792435455
valor integral:  534.7926162189381
Bhatt:  0.6167833339275722
valor integral:  535.4093995528657
Bhatt:  0.45776920628416
valor integral:  535.8671687591499
Bhatt:  0.19239275762958621
valor integral:  536.0595615167795
Bhatt:  0.16560239588927608
valo

valor integral:  877.5085126774461
Bhatt:  0.961951077049834
valor integral:  878.470463754496
Bhatt:  1.0428420288347489
valor integral:  879.5133057833308
Bhatt:  1.0904529490471402
valor integral:  880.603758732378
Bhatt:  1.0474837069651053
valor integral:  881.651242439343
Bhatt:  0.9745431618757587
valor integral:  882.6257856012188
Bhatt:  0.8305724777849687
valor integral:  883.4563580790037
Bhatt:  0.983473534067922
valor integral:  884.4398316130716
Bhatt:  0.9327097780042628
valor integral:  885.3725413910759
Bhatt:  0.9465642194308533
valor integral:  886.3191056105067
Bhatt:  0.8749828247731342
valor integral:  887.1940884352798
Bhatt:  0.8362139595636191
valor integral:  888.0303023948434
Bhatt:  0.7008522749696613
valor integral:  888.731154669813
Bhatt:  0.7634877747323194
valor integral:  889.4946424445453
Bhatt:  0.7646965815396934
valor integral:  890.2593390260851
Bhatt:  0.7148797520517187
valor integral:  890.9742187781368
Bhatt:  0.9701685924964031
valor integral

valor integral:  1271.2541137695582
Bhatt:  0.8938516213506881
valor integral:  1272.147965390909
Bhatt:  0.9724687669735039
valor integral:  1273.1204341578823
Bhatt:  0.9412471525948183
valor integral:  1274.061681310477
Bhatt:  0.9432428822847343
valor integral:  1275.0049241927618
Bhatt:  0.9173468658474909
valor integral:  1275.9222710586093
Bhatt:  0.8356850127975326
valor integral:  1276.7579560714069
Bhatt:  0.9268824346119564
valor integral:  1277.6848385060189
Bhatt:  0.8616775409578528
valor integral:  1278.5465160469766
Bhatt:  0.5969739264691832
valor integral:  1279.1434899734459
Bhatt:  0.8659023497265658
valor integral:  1280.0093923231725
Bhatt:  0.8506003459776613
valor integral:  1280.8599926691502
Bhatt:  0.8540332327307963
valor integral:  1281.714025901881
Bhatt:  0.6441970970730971
valor integral:  1282.3582229989543
Bhatt:  0.25817860005797166
valor integral:  1282.6164015990123
Bhatt:  0.3190431260616973
valor integral:  1282.935444725074
Bhatt:  0.666956274920

...

Bhatt:  0.5585711872885681
valor integral:  14674.18694275277
Bhatt:  0.678595174321024
valor integral:  14674.865537927091
Bhatt:  1.0611642289174854
valor integral:  14675.926702156008
Bhatt:  0.949769513446069
valor integral:  14676.876471669455
Bhatt:  1.0062617145524284
valor integral:  14677.882733384007
Bhatt:  1.0061543704263638
valor integral:  14678.888887754434
Bhatt:  1.1870841827381897
valor integral:  14680.075971937173
Bhatt:  1.0818791017605882
valor integral:  14681.157851038934
Bhatt:  0.38041687560889353
valor integral:  14681.538267914542
Bhatt:  0.6745061588792964
valor integral:  14682.212774073421
Bhatt:  0.7291501066206455
valor integral:  14682.941924180042
Bhatt:  0.6398433998772083
valor integral:  14683.581767579919
Bhatt:  0.7306105845446018
valor integral:  14684.312378164464
Bhatt:  0.6586048529142298
valor integral:  14684.970983017378
Bhatt:  0.7263149332405647
valor integral:  14685.697297950619
Bhatt:  0.7307268006131391
valor integral:  14686.4280247

valor integral:  15069.769247045304
Bhatt:  0.9078942778326692
valor integral:  15070.677141323136
Bhatt:  0.8766624982651767
valor integral:  15071.553803821402
Bhatt:  0.948193100843372
valor integral:  15072.501996922245
Bhatt:  1.0758910667300654
valor integral:  15073.577887988975
Bhatt:  1.0500301635197844
valor integral:  15074.627918152495
Bhatt:  1.1602667387159489
valor integral:  15075.788184891211
Bhatt:  0.8138854662601126
valor integral:  15076.60207035747
Bhatt:  0.816605135836405
valor integral:  15077.418675493307
Bhatt:  0.85614202795919
valor integral:  15078.274817521266
Bhatt:  0.21027562609679162
valor integral:  15078.485093147363
Bhatt:  0.28045761416790815
valor integral:  15078.76555076153
Bhatt:  0.38586664676146226
valor integral:  15079.151417408293
Bhatt:  0.5566977659654946
valor integral:  15079.708115174259
Bhatt:  0.9770759166322722
valor integral:  15080.685191090892
Bhatt:  0.9021037491883452
valor integral:  15081.58729484008
Bhatt:  0.9081274947471

Bhatt:  1.0198402743836874
valor integral:  15449.437057270967
Bhatt:  1.0083088233842843
valor integral:  15450.44536609435
Bhatt:  1.040926530604107
valor integral:  15451.486292624955
Bhatt:  1.0333091193508466
valor integral:  15452.519601744307
Bhatt:  0.835223731958599
valor integral:  15453.354825476265
Bhatt:  0.648577787055903
valor integral:  15454.003403263321
Bhatt:  1.005721856009051
valor integral:  15455.00912511933
Bhatt:  0.9449499189881629
valor integral:  15455.954075038318
Bhatt:  0.8363162530746763
valor integral:  15456.790391291393
Bhatt:  0.7617985980701218
valor integral:  15457.552189889464
Bhatt:  0.9666255897522918
valor integral:  15458.518815479216
Bhatt:  0.8054874007911107
valor integral:  15459.324302880006
Bhatt:  0.9505887140869971
valor integral:  15460.274891594094
Bhatt:  0.9185103730535339
valor integral:  15461.193401967148
Bhatt:  0.9148677311809005
valor integral:  15462.108269698329
Bhatt:  0.8116304551806705
valor integral:  15462.91990015350

valor integral:  15853.390958415619
Bhatt:  0.24381650409081634
valor integral:  15853.63477491971
Bhatt:  0.5436329966395248
valor integral:  15854.17840791635
Bhatt:  0.6112384897827259
valor integral:  15854.789646406132
Bhatt:  0.5977798161521007
valor integral:  15855.387426222285
Bhatt:  0.5526653690505046
valor integral:  15855.940091591336
Bhatt:  0.6036181601019761
valor integral:  15856.543709751437
Bhatt:  0.8286162383818153
valor integral:  15857.372325989818
Bhatt:  0.7757486180258207
valor integral:  15858.148074607843
Bhatt:  1.0087929497625632
valor integral:  15859.156867557605
Bhatt:  0.9338081586674669
valor integral:  15860.090675716272
Bhatt:  0.6856275819490132
valor integral:  15860.77630329822
Bhatt:  0.8474093641811629
valor integral:  15861.623712662402
Bhatt:  0.4025143706314709
valor integral:  15862.026227033033
Bhatt:  0.7817005369542276
valor integral:  15862.807927569987
Bhatt:  0.8483408745004603
valor integral:  15863.656268444487
Bhatt:  0.91736503442

valor integral:  16285.364540701285
Bhatt:  0.6682643701789365
valor integral:  16286.032805071463
Bhatt:  1.0590503367853918
valor integral:  16287.09185540825
Bhatt:  0.18239356627796027
valor integral:  16287.274248974527
Bhatt:  0.20692828557295972
valor integral:  16287.4811772601
Bhatt:  0.5081164611481958
valor integral:  16287.989293721248
Bhatt:  0.5088558335445242
valor integral:  16288.498149554793
Bhatt:  0.9941055802972245
valor integral:  16289.49225513509
Bhatt:  0.42351554059074326
valor integral:  16289.915770675681
Bhatt:  0.39881578130122186
valor integral:  16290.314586456983
Bhatt:  0.7436968076316575
valor integral:  16291.058283264614
Bhatt:  0.18844148545766898
valor integral:  16291.246724750072
Bhatt:  0.15828394991766384
valor integral:  16291.405008699989
Bhatt:  0.3505722850976838
valor integral:  16291.755580985086
Bhatt:  0.18840555181819116
valor integral:  16291.943986536904
Bhatt:  1.242583722431659
valor integral:  16293.186570259335
Bhatt:  1.0446234

In [47]:
print(Correlation_matrix.shape)
print(Correlation_matrix[:3,:3])



(200, 200)
[[    0.         10334.50953253 10685.77589084]
 [    0.             0.         16434.67884152]
 [    0.             0.             0.        ]]
